In [1]:
## Dwa punkty, przestrzeń 2D
## Niech E - punkt startowy uciekającego, P - punkt startowy goniącego
## E porusza się po lini prostej, z prędkością v = const
## P porusza się w kierunku E, z prędkością w = const. Tor P to krzywa pogoni.

## v = (vx, vy)
## w = (E_x-P_x, E_y-P_y)
## Po czasie dt, położenie E będzie
## d(E, dt) = (E_x + vxdt, E_y + vydt)
## Wtedy zaktualizowany wektor prędkości P po upływie czasu dt to
## w = (E_x+vxdt-P_x, E_y+vydt-P_y)



In [1]:
from __future__ import annotations
import math
from dataclasses import dataclass


@dataclass
class Point2D:
    x: float
    y: float

    def __add__(self, val: Point2D) -> Point2D:
        return Point2D(self.x + val.x, self.y + val.y)

    def __sub__(self, val: Point2D) -> Point2D:
        return Point2D(self.x - val.x, self.y - val.y)


class DirectPursuit:
    """Kierunek wprost na cel."""

    def calculate_movement(
        self, pursuer: Point2D, target: Point2D, pursuer_velocity: Point2D
    ) -> Point2D:
        w = target - pursuer
        l = (w.x * w.x + w.y * w.y) ** 0.5
        return Point2D(pursuer_velocity.x * w.x / l, pursuer_velocity.y * w.y / l)


class ConstantBearing:
    """Kierunek do celu, ale odchylony o dany kąt."""

    def __init__(self, bearing_angle_deg: float):
        self.bearing_angle = math.radians(bearing_angle_deg)

    def calculate_movement(
        self, pursuer: Point2D, target: Point2D, pursuer_velocity: Point2D
    ) -> Point2D:
        w = target - pursuer
        angle_to_target = math.atan2(w.y, w.x)
        movement_angle = angle_to_target + self.bearing_angle
        return Point2D(
            pursuer_velocity.x * math.cos(movement_angle),
            pursuer_velocity.y * math.sin(movement_angle),
        )


class ProportionalNavigation:
    """
    Używana w rakietach i pociskach.
    Prędkość kątowa ścigającego jest proporcjonalna do prędkości kątowej linii namiarowania (LOS).
    https://en.wikipedia.org/wiki/Proportional_navigation
    """

    def __init__(self, N: float = 3.0):
        self.N = N
        self.previous_los_angle: float | None = None
        self.previous_pursuer_vel: Point2D | None = None

    def calculate_movement(
        self, pursuer: Point2D, target: Point2D, pursuer_velocity: Point2D
    ) -> Point2D:
        w = target - pursuer
        dist = (w.x * w.x + w.y + w.y) ** 0.5

        los_angle = math.atan2(w.y, w.x)
        if self.previous_los_angle is None:
            self.previous_los_angle = los_angle
            self.previous_pursuer_vel = Point2D(
                pursuer_velocity.x * math.cos(los_angle),
                pursuer_velocity.y * math.sin(los_angle),
            )
            return self.previous_pursuer_vel

        delta_los_angle = los_angle - self.previous_los_angle
        while delta_los_angle > math.pi:
            delta_los_angle -= 2 * math.pi
        while delta_los_angle < -math.pi:
            delta_los_angle += 2 * math.pi

        if self.previous_pursuer_vel is None:
            pursuer_angle = los_angle
        else:
            pursuer_angle = math.atan2(
                self.previous_pursuer_vel.y, self.previous_pursuer_vel.x
            )

        new_pursuer_angle = pursuer_angle + self.N * delta_los_angle
        new_vel = Point2D(
            pursuer_velocity.x * math.cos(new_pursuer_angle),
            pursuer_velocity.y * math.sin(new_pursuer_angle),
        )

        self.previous_los_angle = los_angle
        self.previous_pursuer_vel = new_vel
        return new_vel


class Simulation:
    def __init__(
        self,
        pursuer_start: Point2D,
        target_start: Point2D,
        pursuer_velocity: Point2D,
        target_velocity: Point2D,
        strategy,
        max_iters: int = 1000,
    ):
        self.pursuer_positions = [pursuer_start]
        self.target_positions = [target_start]
        self.pursuer_velocity = pursuer_velocity
        self.target_velocity = target_velocity
        self.strategy = strategy
        self.max_iters = max_iters

    def _step(self) -> tuple[Point2D, Point2D]:
        target = self.target_positions[-1]
        target += self.target_velocity
        self.target_positions.append(target)

        pursuer = self.pursuer_positions[-1]
        movement = self.strategy.calculate_movement(
            pursuer, target, self.pursuer_velocity
        )
        pursuer += movement
        self.pursuer_positions.append(pursuer)

        return pursuer, target

    def _should_stop(self, pursuer: Point2D, target: Point2D) -> bool:
        dx = target.x - pursuer.x
        dy = target.y - pursuer.y
        dist = (dx * dx + dy * dy) ** 0.5
        return dist < 0.45

    def run(self) -> None:
        caught = False
        for i in range(self.max_iters):
            t, p = self._step()
            if self._should_stop(p, t):
                print(f"Złapano cel po {i} krokach.")
                caught = True
                break
        if not caught:
            print(f"Nie udało się złapać celu po {self.max_iters} krokach.")

In [7]:
import numpy as np
from scipy.integrate import solve_ivp
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML


class ContinuousDirectPursuit:
    def __init__(self, target_velocity: tuple[float, float], pursuer_speed: float):
        self.target_velocity = np.array(target_velocity)
        self.pursuer_speed = pursuer_speed

    def dynamics(self, t, state):
        """
        state = [pursuer_x, pursuer_y, target_x, target_y]
        Zwraca pochodne: [dx_p/dt, dy_p/dt, dx_t/dt, dy_t/dt]
        """
        pursuer_pos = state[0:2]
        target_pos = state[2:4]

        # Cel porusza się ze stałą prędkością
        target_vel = self.target_velocity

        # Ścigający leci w kierunku celu
        direction = target_pos - pursuer_pos
        distance = np.linalg.norm(direction)

        if distance < 1e-6:
            pursuer_vel = np.array([0.0, 0.0])
        else:
            pursuer_vel = self.pursuer_speed * direction / distance

        return np.concatenate([pursuer_vel, target_vel])

    def stop_condition(self, t, state):
        """Zatrzymaj gdy odległość < 0.5"""
        pursuer_pos = np.array(state[0:2])
        target_pos = np.array(state[2:4])
        distance = np.linalg.norm(target_pos - pursuer_pos)
        return distance - 0.1

    stop_condition.terminal = True
    stop_condition.direction = -1


def animate_continuous_pursuit(solution, num_frames=200):
    """
    Animacja ciągłego rozwiązania ODE

    Parameters:
    -----------
    solution : OdeResult
        Wynik z solve_ivp
    num_frames : int
        Liczba klatek animacji
    """
    # Interpolacja dla gładkiej animacji
    t_eval = np.linspace(solution.t[0], solution.t[-1], num_frames)

    # Używamy dense_output do interpolacji
    y_interp = solution.sol(t_eval)

    pursuer_x = y_interp[0]
    pursuer_y = y_interp[1]
    target_x = y_interp[2]
    target_y = y_interp[3]

    # Figura
    fig, ax = plt.subplots(figsize=(10, 8))

    # Zakres osi
    all_x = np.concatenate([pursuer_x, target_x])
    all_y = np.concatenate([pursuer_y, target_y])
    margin = 1.0
    ax.set_xlim(all_x.min() - margin, all_x.max() + margin)
    ax.set_ylim(all_y.min() - margin, all_y.max() + margin)

    # Linie trajektorii
    (line_target,) = ax.plot([], [], "r-", label="Target (Cel)", linewidth=2, alpha=0.6)
    (line_pursuer,) = ax.plot(
        [], [], "b-", label="Pursuer (Ścigający)", linewidth=2, alpha=0.6
    )

    # Aktualna pozycja
    (current_target,) = ax.plot([], [], "ro", markersize=15, alpha=0.8)
    (current_pursuer,) = ax.plot([], [], "bo", markersize=15, alpha=0.8)

    # Start i koniec
    ax.plot(target_x[0], target_y[0], "r^", markersize=12, label="Start T")
    ax.plot(pursuer_x[0], pursuer_y[0], "b^", markersize=12, label="Start P")
    ax.plot(target_x[-1], target_y[-1], "rx", markersize=12, label="End T")
    ax.plot(pursuer_x[-1], pursuer_y[-1], "bx", markersize=12, label="End P")

    # Tekst czasu
    time_text = ax.text(
        0.02,
        0.98,
        "",
        transform=ax.transAxes,
        verticalalignment="top",
        fontsize=12,
        bbox=dict(boxstyle="round", facecolor="wheat", alpha=0.5),
    )

    ax.grid(True, alpha=0.3)
    ax.set_xlabel("X", fontsize=12)
    ax.set_ylabel("Y", fontsize=12)
    ax.set_title("Continuous Pursuit Simulation", fontsize=14)
    ax.set_aspect("equal")

    def init():
        line_target.set_data([], [])
        line_pursuer.set_data([], [])
        current_target.set_data([], [])
        current_pursuer.set_data([], [])
        time_text.set_text("")
        return line_target, line_pursuer, current_target, current_pursuer, time_text

    def animate(frame):
        # Trajektoria do tej pory
        line_target.set_data(target_x[: frame + 1], target_y[: frame + 1])
        line_pursuer.set_data(pursuer_x[: frame + 1], pursuer_y[: frame + 1])

        # Aktualna pozycja
        current_target.set_data([target_x[frame]], [target_y[frame]])
        current_pursuer.set_data([pursuer_x[frame]], [pursuer_y[frame]])

        # Czas
        time_text.set_text(f"Time: {t_eval[frame]:.2f}s")

        return line_target, line_pursuer, current_target, current_pursuer, time_text

    anim = animation.FuncAnimation(
        fig,
        animate,
        init_func=init,
        frames=num_frames,
        interval=50,
        blit=True,
        repeat=True,
    )
    plt.close()
    return HTML(anim.to_jshtml())


def run_continuous_simulation():
    # Warunki początkowe: [pursuer_x, pursuer_y, target_x, target_y]
    initial_state = [0.0, 0.0, 10.0, 3.0]

    # Parametry (odpowiadające Twojej symulacji dyskretnej)
    target_velocity = (1.5, -0.5)
    pursuer_speed = np.sqrt(2.2**2 + 1.8**2)  # Prędkość jako moduł

    strategy = ContinuousDirectPursuit(target_velocity, pursuer_speed)

    # Rozwiązanie
    solution = solve_ivp(
        strategy.dynamics,
        t_span=(0, 50),  # Przedział czasu
        y0=initial_state,
        events=strategy.stop_condition,
        dense_output=True,  # WAŻNE: potrzebne do interpolacji
        max_step=0.1,
    )

    print(f"Symulacja zakończona w czasie t={solution.t[-1]:.2f}s")
    print(f"Liczba kroków solwera: {len(solution.t)}")

    return solution


# Uruchomienie
solution = run_continuous_simulation()
animate_continuous_pursuit(solution, num_frames=200)

Symulacja zakończona w czasie t=7.66s
Liczba kroków solwera: 81


In [36]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML


def animate_pursuit(simulation):
    tps = simulation.target_positions
    pps = simulation.pursuer_positions

    fig, ax = plt.subplots(figsize=(8, 8))

    all_x = [point.x for point in tps] + [point.x for point in pps]
    all_y = [point.y for point in tps] + [point.y for point in pps]
    ax.set_xlim(min(all_x) - 1, max(all_x) + 1)
    ax.set_ylim(min(all_y) - 1, max(all_y) + 1)

    (line_target,) = ax.plot(
        [], [], "ro-", label="Target (Cel)", linewidth=2, markersize=8
    )
    (line_pursuer,) = ax.plot(
        [], [], "bo-", label="Pursuer (Ścigający)", linewidth=2, markersize=8
    )

    (current_target,) = ax.plot([], [], "ro", markersize=15, alpha=0.7)
    (current_pursuer,) = ax.plot([], [], "bo", markersize=15, alpha=0.7)

    ax.legend()
    ax.grid(True)
    ax.set_xlabel("X")
    ax.set_ylabel("Y")

    def init():
        line_target.set_data([], [])
        line_pursuer.set_data([], [])
        current_target.set_data([], [])
        current_pursuer.set_data([], [])
        return line_target, line_pursuer, current_target, current_pursuer

    def animate(frame):
        x_coords_target = [tps[i].x for i in range(frame + 1)]
        y_coords_target = [tps[i].y for i in range(frame + 1)]
        line_target.set_data(x_coords_target, y_coords_target)

        x_coords_pursuer = [pps[i].x for i in range(frame + 1)]
        y_coords_pursuer = [pps[i].y for i in range(frame + 1)]
        line_pursuer.set_data(x_coords_pursuer, y_coords_pursuer)

        current_target.set_data([tps[frame].x], [tps[frame].y])
        current_pursuer.set_data([pps[frame].x], [pps[frame].y])

        return line_target, line_pursuer, current_target, current_pursuer

    anim = animation.FuncAnimation(
        fig,
        animate,
        init_func=init,
        frames=len(tps),
        interval=50,
        blit=True,
        repeat=True,
    )
    plt.close()
    return HTML(anim.to_jshtml())


sim = Simulation(
    pursuer_start=Point2D(0.0, 0.0),
    target_start=Point2D(10.0, 3.0),
    pursuer_velocity=Point2D(2.2, 1.8),
    target_velocity=Point2D(1.5, -0.5),
    strategy=ProportionalNavigation(N=3.0),
    max_iters=100,
)
sim.run()
animate_pursuit(sim)

Złapano cel po 14 krokach.
